# Temporal Analysis
*Samantha Feng*

Scripts that assist with the temporal analysis of microcystin and other nutrient concentrations in lakes worldwide.

Analysis was completed using Python via Jupyter Notebook; specific libraries include:
- Pandas
- Plotly
- Scipy
- Pickle

For the most part, various dataframes are being analyzed separately at the moment. This is due to the nature of each of the datasets. Eventually, dataframes for each dataframe will be placed into a single dataframe, and analyzed together.

In [37]:
# Import necessary libraries
import pandas as pd
import pickle
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
from scipy.stats import kendalltau
from collections import defaultdict
import plotly.tools as tools
import re

init_notebook_mode(connected=True)

In [13]:
# Lood data from pickle files into pandas dataframes
florida = pickle.load(open("../data/florida.pkl", "rb"))
alberta = pickle.load(open("../data/alberta.pkl", "rb"))

# Select columns of interest
cols = ['Microcystin (ug/L)', 'Total Nitrogen (ug/L)', 'Total Phosphorus (ug/L)', 'Secchi Depth (m)', 'Total Chlorophyll (ug/L)', 'Temperature (degrees celsius)']

# Format date columns into datetime format
alberta['DATETIME'] = pd.to_datetime(alberta['DATETIME'])
florida['DATETIME'] = pd.to_datetime(florida['DATETIME'])

# Format date of temporal data into 4 seasons a year
alberta['YearSeason'] = pd.to_datetime(alberta['DATETIME']).map(lambda dt: dt.replace(day=1)).map(lambda dt: dt.replace(month=3*((dt.month%12 + 3)//3)-2))
florida['YearSeason'] = pd.to_datetime(florida['DATETIME']).map(lambda dt: dt.replace(day=1)).map(lambda dt: dt.replace(month=3*((dt.month%12 + 3)//3)-2))

# Format date of temporal data into 12 months a year
alberta['YearMonth'] = pd.to_datetime(alberta['DATETIME']).map(lambda dt: dt.replace(day=1))
florida['YearMonth'] = pd.to_datetime(florida['DATETIME']).map(lambda dt: dt.replace(day=1))

In [3]:
# Concatentate various dataframes into a single one, for future use
frames = [florida, alberta]
data = pd.concat(frames)

/home/samfeng/.local/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




## Plotting data against time

- The raw data was plotted against time, enabling viewers to note temporal trends in the parameters.
- The time axis was attempted with monthly bins, as well as seasonal bins.
- Data more than 3 SD was stripped to see the results.
- Overall monthly averages were taken. 

In [44]:
# Plot all relevant data with no change to date for each column of interest
for c in cols:
    # Strip text in brackets from column name for graph title
    c_stripped = re.sub("[\(\[].*?[\)\]]", "", c)
    c_stripped = re.sub('\s+', ' ', c_stripped).strip()
    
    alberta_x=alberta['DATETIME']
    alberta_y=alberta[c]

    florida_x=florida['DATETIME']
    florida_y=florida[c]
    
    layout = go.Layout(
        title= f'{c_stripped} vs Date', 
        xaxis={'title':'Date'}, 
        yaxis={'title': c}
    )

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Alberta'
    )

    f = go.Scatter(
        x=florida_x,
        y=florida_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Florida'
    )

    fig = {
        'data': [f, a],
        'layout': layout
    }

    iplot(fig)

In [43]:
# Plot all relevant data by season and by month for each column of interest
for c in cols:
    # Strip text in brackets from column name for graph title
    c_stripped = re.sub("[\(\[].*?[\)\]]", "", c)
    c_stripped = re.sub('\s+', ' ', c_stripped).strip()
    
    # Plot all relevant data by season
    alberta_x=alberta['YearSeason']
    alberta_y=alberta[c]

    florida_x=florida['YearSeason']
    florida_y=florida[c]
    
    layout = go.Layout(
        title= f'{c_stripped} vs Date (Seasonally)', 
        xaxis={'title':'Date'}, 
        yaxis={'title': c}
    )

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Alberta'
    )

    f = go.Scatter(
        x=florida_x,
        y=florida_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Florida'
    )

    fig = {
        'data': [f, a],
        'layout': layout
    }

    iplot(fig)

    # Plot all relevant data by month
    alberta_x=alberta['YearMonth']
    alberta_y=alberta[c]

    florida_x=florida['YearMonth']
    florida_y=florida[c]
    
    layout = go.Layout(
        title= f'{c_stripped} vs Date (Monthly)', 
        xaxis={'title':'Date'}, 
        yaxis={'title': c}
    )

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Alberta'
    )

    f = go.Scatter(
        x=florida_x,
        y=florida_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Florida'
    )

    fig = {
        'data': [f, a],
        'layout': layout
    }

    iplot(fig)

In [42]:
# Plot values within 3 standard deviations by month and by season for each column of interest
for c in cols:
    # Strip text in brackets from column name for graph title
    c_stripped = re.sub("[\(\[].*?[\)\]]", "", c)
    c_stripped = re.sub('\s+', ' ', c_stripped).strip()
    
    # Strip values more than 3 standard deviations away
    alberta_2 = alberta[((alberta[c] - alberta[c].mean()) / alberta[c].std()).abs() < 3]
    florida_2 = florida[((florida[c] - florida[c].mean()) / florida[c].std()).abs() < 3]
    
    # Plot monthly data - values more than 3 SD away stripped
    alberta_x=alberta_2['YearMonth']
    alberta_y=alberta_2[c]

    florida_x=florida_2['YearMonth']
    florida_y=florida_2[c]
    
    layout = go.Layout(
        title= f'{c_stripped} vs Date - 3 SD (Monthly)', 
        xaxis={'title':'Date'}, 
        yaxis={'title': c}
    )

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Alberta'
    )

    f = go.Scatter(
        x=florida_x,
        y=florida_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Florida'
    )

    fig = {
        'data': [f, a],
        'layout': layout
    }

    iplot(fig)
    
    # Plot seasonal data - values more than 3 SD away stripped
    alberta_x=alberta_2['YearSeason']
    alberta_y=alberta_2[c]

    florida_x=florida_2['YearSeason']
    florida_y=florida_2[c]
    
    layout = go.Layout(
        title= f'{c_stripped} vs Date - 3 SD (Seasonally)', 
        xaxis={'title':'Date'}, 
        yaxis={'title': c}
    )

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Alberta'
    )

    f = go.Scatter(
        x=florida_x,
        y=florida_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Florida'
    )

    fig = {
        'data': [f, a],
        'layout': layout
    }

    iplot(fig)

## In-Depth Analysis

The more in-depth analysis was performed on the Alberta data specifically, on monthly basis.

In [7]:
# Aggregate Alberta data specifically by months
months = alberta.DATETIME.dt.to_period("M")
a_month = alberta.groupby(months)
a_month = a_month.agg(['sum', 'mean', 'std'])

In [45]:
# Plot overall monthly averages and monthly percent changes of each column of interest
for c in cols:
    # Strip text in brackets from column name for graph title
    c_stripped = re.sub("[\(\[].*?[\)\]]", "", c)
    c_stripped = re.sub('\s+', ' ', c_stripped).strip()
    
    # Make a 2x1 grid of plots 
    fig = tools.make_subplots(rows=2, cols=1, subplot_titles=(f'{c_stripped} vs Date', f'% Change of {c_stripped} vs Date'), print_grid=False)
    
    # Evaluate the mean and percent change
    alberta_x=a_month.index.to_timestamp()
    alberta_y=a_month[c]['mean']
    alberta_y_percent=a_month[c]['mean'].pct_change()

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Average'
    )
    
    a_percent = go.Scatter(
        x=alberta_x,
        y=alberta_y_percent,
        mode='markers',
        marker={
       'opacity': 0.6,
        },
        name='Average % Change'
    )
    
    fig.append_trace(a, 1, 1)
    fig.append_trace(a_percent, 2, 1)
     
    fig['layout']['yaxis1'].update(title=c)
    fig['layout']['xaxis2'].update(title='Date')
    fig['layout']['yaxis2'].update(title=f'% Change of {c}')

    iplot(fig)

In [46]:
# Copy dataframe to run lake-specific tasks
alberta_grouped = alberta.copy()

# Divide microcystin by chlorophyll to see if data is 'normalized'
alberta_grouped['Normalized Microcystin'] = alberta_grouped['Microcystin (ug/L)']/alberta_grouped['Total Chlorophyll (ug/L)']

# Bin data into 6 groups by lake alphabetically (would like to do this laditudinally/longitudinally eventually)
n_bins = 6;
alberta_grouped['graph'] = pd.cut(alberta_grouped.index, bins=n_bins, labels=False) + 1
grouped = alberta_grouped.groupby('Body of Water Name')

# Create an empty default dictionary to store binned microcystin plots 
lakes_mc = defaultdict(list)

# Create an empty default dictionary to store % change of microcystin plots
lakes_mc_pc = defaultdict(list)

# Create an empty default dictionary to store binned microcystin/chlorophyll, or normalized microcystin plots
lakes_mc_norm = defaultdict(list)

In [35]:
# Layout is identical and established first
layout = go.Layout(
    title= 'Microcystin per Lake vs Date', 
    xaxis={'title':'Date'}, 
    yaxis={'title': 'Microcystin (ug/L)'}
)

# For each lake, take microcystin data by month and plot against time
for name, group in grouped:
    graph_num = int(group['graph'].head(1))
    alberta_x=group['DATETIME']
    alberta_y=group['Microcystin (ug/L)']

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='lines',
        marker={
           'opacity': 0.8,
        },
        line = {
            'width': 1.5},
        name=f'{name}'
    )
    
    # Append plot to a specific graph based on bin number
    lakes_mc[graph_num].append(a)

# Generate visualization
for i in range(1, n_bins):
    fig = {
        'data': lakes_mc[i],
        'layout': layout
    }

    iplot(fig)

In [36]:
# Layout is the same per for each group
layout = go.Layout(
    title= '% Change of Microcystin per Lake vs Date', 
    xaxis={'title':'Date'}, 
    yaxis={'title': 'Microcystin (ug/L)'}
)

# For each lake, calculate the percent change in microcystin by month and plot against time
for name, group in grouped:
    graph_num = int(group['graph'].head(1))
    alberta_x=group['DATETIME']
    alberta_y=group['Microcystin (ug/L)'].pct_change()

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='lines',
        marker={
           'opacity': 0.8,
        },
        line = {
            'width': 1.5},
        name=f'{name}'
    )
    
    # Append plot to a specific graph based on bin number
    lakes_mc_pc[graph_num].append(a)

# Create visualization
for i in range(1, n_bins):
    fig = {
        'data': lakes_mc_pc[i],
        'layout': layout
    }

    iplot(fig)

In [47]:
# Layout is identical and established first
layout = go.Layout(
    title= 'Microcystin/Chlorophyll per Lake vs Date', 
    xaxis={'title':'Date'}, 
    yaxis={'title': 'Microcystin/Chlorophyll'}
)

# For each lake, take normalized microcystin data and plot against time
for name, group in grouped:
    graph_num = int(group['graph'].head(1))
    alberta_x=group['DATETIME']
    alberta_y=group['Normalized Microcystin']

    a = go.Scatter(
        x=alberta_x,
        y=alberta_y,
        mode='lines',
        marker={
           'opacity': 0.8,
        },
        line = {
            'width': 1.5},
        name=f'{name}'
    )
    
    # Append plot to a specific graph
    lakes_mc_norm[graph_num].append(a)

# Plot all graphs
for i in range(1, n_bins):
    fig = {
        'data': lakes_mc_norm[i],
        'layout': layout
    }

    iplot(fig)


In [76]:
# Mann-Kendall values
mk = alberta.groupby(['Body of Water Name']).apply(lambda x: kendalltau(x['DATETIME'], x['Microcystin (ug/L)'])).reset_index()
mk = mk.rename(columns={0: 'MK'})
for index, row in mk.iterrows():
    print(row['Body of Water Name'], row['MK'].correlation)

ADAMSON LAKE -0.10540925533894598
AMISK LAKE -0.7378647873726218
ARM LAKE 0.18257418583505539
ASTOTIN LAKE 0.19999999999999998
BAPTISTE LAKE - NORTH BASIN 0.5544826240669376
BAPTISTE LAKE - SOUTH BASIN 0.4437475344939221
BEARTRAP LAKE -0.03077287274483318
BEAUVAIS LAKE -0.18212504816617942
BEAVER LAKE -0.19999999999999998
BELLEVUE LAKE 1.0
BIG LAKE EAST/WEST BASIN COMP (AB05EA1550) 1.0
BITTERN LAKE nan
BLACKFALDS LAKE -0.33333333333333337
BUCK LAKE 1.0
CLAIRMONT LAKE -0.2
CLEAR LAKE 0.33333333333333337
CLEAR LAKE (BARNS LAKE) 0.1079583792718826
COOKING LAKE 0.3571428571428571
COW LAKE 0.816496580927726
CRIMSON LAKE 0.11503946170861014
DILLBERRY LAKE 0.06726727939963124
DRIEDMEAT LAKE 0.33333333333333337
EAGLE LAKE nan
ELKWATER LAKE 0.02853069950072753
ETHEL LAKE (NEAR COLD LAKE) 0.0
FISHING LAKE 0.19999999999999998
FLYINGSHOT LAKE 0.6666666666666669
FORK LAKE 0.34641016151377546
FROG LAKE -0.9128709291752769
GARNIER LAKE (BLUET) - SOUTH BASIN -0.22360679774997896
GARNIER LAKE - NORTH B

## Future Analysis
- Determine an intuitive and informational way to plot Mann-Kendall values per lake
- Bin lake data by geographic location rather than alphabetically
- Incorporate larger datasets with more variety of location, and possibly larger time span